# rs_bernsteinCorrection
Example of the BernsteinCorrection utility in RooStats.

The idea is that one has a distribution coming either from data or Monte Carlo
(called "reality" in the macro) and a nominal model that is not sufficiently
flexible to take into account the real distribution.  One wants to take into
account the systematic associated with this imperfect modeling by augmenting
the nominal model with some correction term (in this case a polynomial).
The BernsteinCorrection utility will import into your workspace a corrected model
given by nominal(x) * poly_N(x), where poly_N is an n-th order polynomial in
the Bernstein basis.  The degree N of the polynomial is chosen by specifying the tolerance
one has in adding an extra term to the polynomial.
The Bernstein basis is nice because it only has positive-definite terms
and works well with PDFs.
Finally, the macro makes a plot of:
 - the data (drawn from 'reality'),
 - the best fit of the nominal model (blue)
 - and the best fit corrected model.




**Author:** Kyle Cranmer  
<i><small>This notebook tutorial was automatically generated with <a href= "https://github.com/root-project/root/blob/master/documentation/doxygen/converttonotebook.py">ROOTBOOK-izer</a> from the macro found in the ROOT repository  on Wednesday, April 17, 2024 at 11:20 AM.</small></i>

In [1]:
%%cpp -d
#include "RooDataSet.h"
#include "RooRealVar.h"
#include "RooConstVar.h"
#include "RooBernstein.h"
#include "TCanvas.h"
#include "RooAbsPdf.h"
#include "RooFitResult.h"
#include "RooPlot.h"
#include <string>
#include <vector>
#include <stdio.h>
#include <sstream>
#include <iostream>

#include "RooProdPdf.h"
#include "RooAddPdf.h"
#include "RooGaussian.h"
#include "RooProfileLL.h"
#include "RooWorkspace.h"

#include "RooStats/BernsteinCorrection.h"

using namespace RooFit;
using namespace RooStats;

set range of observable

In [2]:
Double_t lowRange = -1, highRange = 5;

make a RooRealVar for the observable

In [3]:
RooRealVar x("x", "x", lowRange, highRange);

true model

In [4]:
RooGaussian narrow("narrow", "", x, RooConst(0.), RooConst(.8));
RooGaussian wide("wide", "", x, RooConst(0.), RooConst(2.));
RooAddPdf reality("reality", "", RooArgList(narrow, wide), RooConst(0.8));

std::unique_ptr<RooDataSet> data{reality.generate(x, 1000)};

input_line_50:6:1: warning: 'data' shadows a declaration with the same name in the 'std' namespace; use '::data' to reference this declaration
std::unique_ptr<RooDataSet> data{reality.generate(x, 1000)};
^


nominal model

In [5]:
RooRealVar sigma("sigma", "", 1., 0, 10);
RooGaussian nominal("nominal", "", x, RooConst(0.), sigma);

RooWorkspace *wks = new RooWorkspace("myWorksspace");

wks->import(*data, Rename("data"));
wks->import(nominal);

if (TClass::GetClass("ROOT::Minuit2::Minuit2Minimizer")) {
   // use Minuit2 if ROOT was built with support for it:
   ROOT::Math::MinimizerOptions::SetDefaultMinimizer("Minuit2");
}

input_line_51:7:14: error: reference to 'data' is ambiguous
wks->import(*data, Rename("data"));
             ^
input_line_50:6:29: note: candidate found by name lookup is 'data'
std::unique_ptr<RooDataSet> data{reality.generate(x, 1000)};
                            ^
/usr/include/c++/9/bits/range_access.h:318:5: note: candidate found by name lookup is 'std::data'
    data(initializer_list<_Tp> __il) noexcept
    ^
/usr/include/c++/9/bits/range_access.h:289:5: note: candidate found by name lookup is 'std::data'
    data(_Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:299:5: note: candidate found by name lookup is 'std::data'
    data(const _Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:309:5: note: candidate found by name lookup is 'std::data'
    data(_Tp (&__array)[_Nm]) noexcept
    ^


The tolerance sets the probability to add an unnecessary term.
lower tolerance will add fewer terms, while higher tolerance
will add more terms and provide a more flexible function.

In [6]:
Double_t tolerance = 0.05;
BernsteinCorrection bernsteinCorrection(tolerance);
Int_t degree = bernsteinCorrection.ImportCorrectedPdf(wks, "nominal", "x", "data");

if (degree < 0) {
   Error("rs_bernsteinCorrection", "Bernstein correction failed ! ");
   return;
}

cout << " Correction based on Bernstein Poly of degree " << degree << endl;

RooPlot *frame = x.frame();
data->plotOn(frame);

input_line_52:14:1: error: reference to 'data' is ambiguous
data->plotOn(frame);
^
input_line_50:6:29: note: candidate found by name lookup is 'data'
std::unique_ptr<RooDataSet> data{reality.generate(x, 1000)};
                            ^
/usr/include/c++/9/bits/range_access.h:318:5: note: candidate found by name lookup is 'std::data'
    data(initializer_list<_Tp> __il) noexcept
    ^
/usr/include/c++/9/bits/range_access.h:289:5: note: candidate found by name lookup is 'std::data'
    data(_Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:299:5: note: candidate found by name lookup is 'std::data'
    data(const _Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:309:5: note: candidate found by name lookup is 'std::data'
    data(_Tp (&__array)[_Nm]) noexcept
    ^


plot the best fit nominal model in blue

In [7]:
 nominal.fitTo(*data, PrintLevel(0));
nominal.plotOn(frame);

input_line_53:2:18: error: reference to 'data' is ambiguous
  nominal.fitTo(*data, PrintLevel(0));
                 ^
input_line_50:6:29: note: candidate found by name lookup is 'data'
std::unique_ptr<RooDataSet> data{reality.generate(x, 1000)};
                            ^
/usr/include/c++/9/bits/range_access.h:318:5: note: candidate found by name lookup is 'std::data'
    data(initializer_list<_Tp> __il) noexcept
    ^
/usr/include/c++/9/bits/range_access.h:289:5: note: candidate found by name lookup is 'std::data'
    data(_Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:299:5: note: candidate found by name lookup is 'std::data'
    data(const _Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:309:5: note: candidate found by name lookup is 'std::data'
    data(_Tp (&__array)[_Nm]) noexcept
    ^
input_line_53:3:1: error: use of undeclared identifier 'nominal'
nominal.plotOn(frame);
^
i

plot the best fit corrected model in red

In [8]:
RooAbsPdf *corrected = wks->pdf("corrected");
if (!corrected)
   return;

input_line_55:2:3: error: use of undeclared identifier 'wks'
 (wks->pdf("corrected"))
  ^
Error in <HandleInterpreterException>: Error evaluating expression (wks->pdf("corrected"))
Execution of your code was aborted.


fit corrected model

In [9]:
corrected->fitTo(*data, PrintLevel(0));
corrected->plotOn(frame, LineColor(kRed));

input_line_56:2:20: error: reference to 'data' is ambiguous
 corrected->fitTo(*data, PrintLevel(0));
                   ^
input_line_50:6:29: note: candidate found by name lookup is 'data'
std::unique_ptr<RooDataSet> data{reality.generate(x, 1000)};
                            ^
/usr/include/c++/9/bits/range_access.h:318:5: note: candidate found by name lookup is 'std::data'
    data(initializer_list<_Tp> __il) noexcept
    ^
/usr/include/c++/9/bits/range_access.h:289:5: note: candidate found by name lookup is 'std::data'
    data(_Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:299:5: note: candidate found by name lookup is 'std::data'
    data(const _Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:309:5: note: candidate found by name lookup is 'std::data'
    data(_Tp (&__array)[_Nm]) noexcept
    ^
input_line_56:3:19: error: use of undeclared identifier 'frame'
corrected->plotOn(frame

plot the correction term (* norm constant) in dashed green
should make norm constant just be 1, not depend on binning of data

In [10]:
RooAbsPdf *poly = wks->pdf("poly");
if (poly)
   poly->plotOn(frame, LineColor(kGreen), LineStyle(kDashed));

input_line_57:4:34: error: cannot take the address of an rvalue of type 'EColor'
   poly->plotOn(frame, LineColor(kGreen), LineStyle(kDashed));
                                 ^~~~~~
Error while creating dynamic expression for:
  poly->plotOn(frame, LineColor(kGreen), LineStyle(kDashed))


this is a switch to check the sampling distribution
of -2 log LR for two comparisons:
the first is for n-1 vs. n degree polynomial corrections
the second is for n vs. n+1 degree polynomial corrections
Here we choose n to be the one chosen by the tolerance
criterion above, eg. n = "degree" in the code.
Setting this to true is takes about 10 min.

In [11]:
bool checkSamplingDist = true;
int numToyMC = 20; // increase this value for sensible results

TCanvas *c1 = new TCanvas();
if (checkSamplingDist) {
   c1->Divide(1, 2);
   c1->cd(1);
}
frame->Draw();
gPad->Update();

if (checkSamplingDist) {
   // check sampling dist
   ROOT::Math::MinimizerOptions::SetDefaultPrintLevel(-1);
   TH1F *samplingDist = new TH1F("samplingDist", "", 20, 0, 10);
   TH1F *samplingDistExtra = new TH1F("samplingDistExtra", "", 20, 0, 10);
   bernsteinCorrection.CreateQSamplingDist(wks, "nominal", "x", "data", samplingDist, samplingDistExtra, degree,
                                           numToyMC);

   c1->cd(2);
   samplingDistExtra->SetLineColor(kRed);
   samplingDistExtra->Draw();
   samplingDist->Draw("same");
}

[runStaticInitializersOnce]: Failed to materialize symbols: { (main, { $.cling-module-321.__inits.0, __orc_init_func.cling-module-321, _ZN12__cling_N52917checkSamplingDistE, _ZN12__cling_N5292c1E, __cxx_global_var_initcling_module_321_, _ZN12__cling_N52916__cling_Un1Qu329EPv, _GLOBAL__sub_I_cling_module_321, _ZN12__cling_N5298numToyMCE, _ZN7TObjectnwEm }) }
IncrementalExecutor::executeFunction: symbol '_ZN5cling7runtime8internal9EvaluateTIvEET_PNS1_15DynamicExprInfoEPN5clang11DeclContextE' unresolved while linking [cling interface function]!
You are probably missing the definition of void cling::runtime::internal::EvaluateT<void>(cling::runtime::internal::DynamicExprInfo*, clang::DeclContext*)
Maybe you need to load the corresponding shared library?


Draw all canvases 

In [12]:
%jsroot on
gROOT->GetListOfCanvases()->Draw()